In [28]:
import ccxt
import pandas as pd
from datetime import datetime, timedelta
import random
import numpy as np
from tensortrade.env.default import create
from tensortrade.env.default.rewards import SimpleProfit
from tensortrade.env.default.actions import ManagedRiskOrders
from tensortrade.feed.core import DataFeed, Stream
from tensortrade.oms.instruments import USD, BTC
from tensortrade.oms.wallets import Wallet, Portfolio
from tensortrade.oms.exchanges import Exchange

import pandas as pd
import plotly.graph_objects as go
import plotly.express as px

In [6]:
import ccxt
import pandas as pd
from datetime import datetime, timedelta

# Initialiser l'API Binance
exchange = ccxt.binance()

# Fonction pour obtenir des données OHLCV
def fetch_binance_data(symbol, timeframe, since, limit=1000):
    data = exchange.fetch_ohlcv(symbol, timeframe, since=since, limit=limit)
    df = pd.DataFrame(data, columns=['timestamp', 'open', 'high', 'low', 'close', 'volume'])
    df['timestamp'] = pd.to_datetime(df['timestamp'], unit='ms')
    return df

# Fonction principale pour récupérer les données par morceaux et les concaténer
def get_historical_data(symbol, timeframe, start_date, end_date):
    start_time = datetime.strptime(start_date, '%Y-%m-%dT%H:%M:%SZ')
    end_time = datetime.strptime(end_date, '%Y-%m-%dT%H:%M:%SZ')
    delta = timedelta(minutes=1000)  # Intervalle de 1000 minutes
    all_data = []

    while start_time < end_time:
        temp_end_time = start_time + delta
        if temp_end_time > end_time:
            temp_end_time = end_time

        since = int(start_time.timestamp() * 1000)
        df = fetch_binance_data(symbol, timeframe, since=since)

        if df.empty:
            break

        all_data.append(df)
        start_time = df['timestamp'].iloc[-1] + timedelta(minutes=1)  # Passer à la minute suivante

    # Concaténer toutes les données
    full_data = pd.concat(all_data, ignore_index=True)
    return full_data

# Exemple d'utilisation
symbol = "BTC/USDT"
timeframe = "1m"  # Intervalle d'une minute
start_date = "2024-11-25T00:00:00Z"  # Format complet avec année, mois, jour, heure et minute
end_date = "2024-12-09T23:59:59Z"  # Format complet avec année, mois, jour, heure et minute

df1 = get_historical_data(symbol, timeframe, start_date, end_date)

# Sauvegarde des données dans un fichier CSV
#df.to_csv('historical_data.csv', index=False)


# Data Preparation

In [ ]:
df = df1

# Génération des signaux d'entrée
df['Signal'] = np.random.choice([1, -1], size=len(df))º

# Initialisation des colonnes pour les niveaux de sortie
df['Take_Profit'] = None
df['Stop_Loss'] = None
df['Position_Closed'] = False

# Paramètres de la stratégie
take_profit_pct = 0.3  # 2% de profit
stop_loss_pct = 0.2   # 1% de perte

# Logique pour définir les niveaux de Take Profit et Stop Loss
current_position = None
entry_price = None

for i in range(len(df)):
    if current_position is None:  # Pas de position ouverte
        if df.loc[i, 'Signal'] == 1:  # Signal d'achat
            current_position = 'long'
            entry_price = df.loc[i, 'close']
            df.loc[i, 'Take_Profit'] = entry_price * (1 + take_profit_pct)
            df.loc[i, 'Stop_Loss'] = entry_price * (1 - stop_loss_pct)
        elif df.loc[i, 'Signal'] == -1:  # Signal de vente (short)
            current_position = 'short'
            entry_price = df.loc[i, 'close']
            df.loc[i, 'Take_Profit'] = entry_price * (1 - take_profit_pct)
            df.loc[i, 'Stop_Loss'] = entry_price * (1 + stop_loss_pct)
    else:  # Une position est ouverte
        if current_position == 'long':  # Position d'achat
            if (
                pd.notna(df.loc[i - 1, 'Take_Profit']) and df.loc[i, 'high'] >= df.loc[i - 1, 'Take_Profit']
            ) or (
                pd.notna(df.loc[i - 1, 'Stop_Loss']) and df.loc[i, 'low'] <= df.loc[i - 1, 'Stop_Loss']
            ):
                df.loc[i, 'Position_Closed'] = True
                current_position = None
                entry_price = None
        elif current_position == 'short':  # Position de vente
            if (
                pd.notna(df.loc[i - 1, 'Take_Profit']) and df.loc[i, 'low'] <= df.loc[i - 1, 'Take_Profit']
            ) or (
                pd.notna(df.loc[i - 1, 'Stop_Loss']) and df.loc[i, 'high'] >= df.loc[i - 1, 'Stop_Loss']
            ):
                df.loc[i, 'Position_Closed'] = True
                current_position = None
                entry_price = None
df

timestamp      open      high       low     close    volume  \
0     2024-11-24 23:00:00  97999.99  98000.00  97918.60  97965.24  34.37477   
1     2024-11-24 23:01:00  97965.24  97991.99  97965.24  97972.58  16.63760   
2     2024-11-24 23:02:00  97972.58  98045.00  97959.61  98024.01  68.44312   
3     2024-11-24 23:03:00  98024.00  98100.00  98009.64  98100.00  89.95844   
4     2024-11-24 23:04:00  98100.00  98118.14  98095.99  98118.13  29.25932   
...                   ...       ...       ...       ...       ...       ...   
21995 2024-12-10 05:35:00  96759.98  96854.25  96759.98  96830.31  20.38103   
21996 2024-12-10 05:36:00  96830.31  96830.31  96742.00  96764.00  10.35646   
21997 2024-12-10 05:37:00  96764.00  96910.05  96756.00  96850.78  68.54551   
21998 2024-12-10 05:38:00  96850.78  96930.23  96850.78  96886.50  52.59316   
21999 2024-12-10 05:39:00  96886.50  96886.51  96840.00  96840.01   6.37762   

             MACD  Signal_Line  Signal Take_Profit  Stop_Loss  \
0        0.000000     0.000000     NaN        None       None   
1        0.006579     0.000013     1.0  127364.354  78378.064   
2        0.059241     0.000131     1.0        None       None   
3        0.179888     0.000491    -1.0        None       None   
4        0.316492     0.001122     1.0        None       None   
...           ...          ...     ...         ...        ...   
21995 -697.866338  -479.016971    -1.0        None       None   
21996 -698.131876  -479.454763     1.0        None       None   
21997 -698.318088  -479.892053    -1.0        None       None   
21998 -698.470936  -480.328774    -1.0        None       None   
21999 -698.664188  -480.765008     1.0        None       None   

       Position_Closed  PnL  Cumulative_PnL Status  
0                False    0               0    NaN  
1                False    0               0  Achat  
2                False    0               0  Achat  
3                False    0               0  Achat  
4                False    0               0  Achat  
...                ...  ...             ...    ...  
21995            False    0               0  Achat  
21996            False    0               0  Achat  
21997            False    0               0  Achat  
21998            False    0               0  Achat  
21999            False    0               0  Achat  

[22000 rows x 15 columns]

In [30]:
df.to_excel('C:\\Python\\Trading Strategie Based on Data and ML\\Data\\historical_data.xlsx', index=False)

PermissionError: [Errno 13] Permission denied: 'C:\\Python\\Trading Strategie Based on Data and ML\\Data\\historical_data.xlsx'

In [24]:
pip install openpyxl

  Using cached openpyxl-3.1.5-py2.py3-none-any.whl.metadata (2.5 kB)
  Using cached et_xmlfile-2.0.0-py3-none-any.whl.metadata (2.7 kB)
Using cached openpyxl-3.1.5-py2.py3-none-any.whl (250 kB)
Using cached et_xmlfile-2.0.0-py3-none-any.whl (18 kB)
Note: you may need to restart the kernel to use updated packages.


In [31]:
# Initialisation des colonnes
df['PnL'] = 0  # Profits et pertes par trade
df['Cumulative_PnL'] = 0  # Profits cumulés

# Variables pour le suivi des positions
current_position = None
entry_price = None

# Calcul des profits et pertes pour chaque trade
for i in range(len(df)):
    if current_position is None:  # Pas de position ouverte
        if df.loc[i, 'Signal'] == 1:  # Signal d'achat
            current_position = 'long'
            entry_price = df.loc[i, 'close']
        elif df.loc[i, 'Signal'] == -1:  # Signal de vente
            current_position = 'short'
            entry_price = df.loc[i, 'close']
    else:  # Une position est ouverte
        if df.loc[i, 'Position_Closed']:  # La position est fermée
            if current_position == 'long':  # Achat fermé
                df.loc[i, 'PnL'] = df.loc[i, 'close'] - entry_price
            elif current_position == 'short':  # Vente fermée
                df.loc[i, 'PnL'] = entry_price - df.loc[i, 'close']
            current_position = None
            entry_price = None

# Calcul des profits cumulés
df['Cumulative_PnL'] = df['PnL'].cumsum()

# Ajout de l'état de la stratégie dans la DataFrame
df['Status'] = df['Signal'].replace({1: 'Achat', -1: 'Vente', 0: 'Neutre'})


In [32]:


# Ajout de la colonne des profits cumulés
df['Cumulative_PnL'] = df['PnL'].cumsum()

# 1. Visualisation des profits cumulés
fig_cumulative_pnl = px.line(df, x='timestamp', y='Cumulative_PnL', title="Évolution des Profits Cumulés")
fig_cumulative_pnl.update_layout(xaxis_title="Temps", yaxis_title="Profits (€)")
fig_cumulative_pnl.show()

# 2. Graphique en chandeliers avec signaux d'achat et de vente
fig_candlestick = go.Figure(data=[
    go.Candlestick(
        x=df['timestamp'],
        open=df['open'],
        high=df['high'],
        low=df['low'],
        close=df['close'],
        name='Prix'
    )
])

# Ajout des signaux d'achat
buy_signals = df[df['Signal'] == 1]
fig_candlestick.add_trace(go.Scatter(
    x=buy_signals['timestamp'],
    y=buy_signals['close'],
    mode='markers',
    marker=dict(color='green', symbol='triangle-up', size=10),
    name='Signal Achat'
))

# Ajout des signaux de vente
sell_signals = df[df['Signal'] == -1]
fig_candlestick.add_trace(go.Scatter(
    x=sell_signals['timestamp'],
    y=sell_signals['close'],
    mode='markers',
    marker=dict(color='red', symbol='triangle-down', size=10),
    name='Signal Vente'
))

fig_candlestick.update_layout(
    title="Graphique des Chandeliers Japonais avec Signaux de Trading",
    xaxis_title="Temps",
    yaxis_title="Prix (€)",
    xaxis_rangeslider_visible=False
)
fig_candlestick.show()

# 3. Histogramme des profits et pertes
fig_histogram = px.histogram(df, x='PnL', nbins=50, title="Répartition des Profits et Pertes")
fig_histogram.update_layout(xaxis_title="Profit ou Perte (€)", yaxis_title="Fréquence")
fig_histogram.show()

# 4. Résumé des performances
total_profit = df['PnL'].sum()
winning_trades = df[df['PnL'] > 0]['PnL'].count()
losing_trades = df[df['PnL'] <= 0]['PnL'].count()
win_rate = (winning_trades / (winning_trades + losing_trades)) * 100

performance_summary = f"""
Résumé des Performances de la Stratégie :
- Total des Profits : {total_profit:.2f} €
- Nombre de Trades Gagnants : {winning_trades}
- Nombre de Trades Perdants : {losing_trades}
- Taux de Succès : {win_rate:.2f}%
"""

print(performance_summary)




Résumé des Performances de la Stratégie :
- Total des Profits : 0.00 €
- Nombre de Trades Gagnants : 0
- Nombre de Trades Perdants : 22000
- Taux de Succès : 0.00%

